In [1]:
import pandas as pd
import numpy as np
import pickle
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.grid_search import GridSearchCV

C:\Users\DELL\Anaconda3\lib\site-packages\sklearn\ensemble\weight_boosting.py:29: DeprecationWarning: numpy.core.umath_tests is an internal NumPy module and should not be imported. It will be removed in a future NumPy release.
  from numpy.core.umath_tests import inner1d
C:\Users\DELL\Anaconda3\lib\site-packages\sklearn\cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)
C:\Users\DELL\Anaconda3\lib\site-packages\sklearn\grid_search.py:42: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. This module will be removed in 0.20.
  DeprecationWarning)


In [2]:
from openpyxl import Workbook,load_workbook

In [3]:
import os

In [4]:
from sklearn.metrics import r2_score,mean_squared_error,precision_score,recall_score,accuracy_score,confusion_matrix

In [5]:
os.chdir('../output_data')

In [6]:
df = pd.read_csv('train_v04.csv',header=0)

In [5]:
ignore_cols = ['Symbol','Series','Date','Prev_Close','Open','Close','Prev_Close_min','Prev_Close_max','Sector']

In [6]:
os.chdir('../pickles')

In [7]:
numerical = pickle.load(open('numerical.pickle','rb'))
categorical = pickle.load(open('categorical.pickle','rb'))
conversion_dict = pickle.load(open('conversion_dict.pickle','rb'))
imputation_cols = pickle.load(open('imputation_cols.pickle','rb'))
model_columns = pickle.load(open('model_columns.pickle','rb'))
lr_model_columns = pickle.load(open('lr_model_columns.pickle','rb'))
order = pickle.load(open('order.pickle','rb'))
pca = pickle.load(open('pca.pickle','rb'))
scale = pickle.load(open('scale.pickle','rb'))

In [8]:
from keras.layers import Input,Dense,Dropout

Using TensorFlow backend.


In [9]:
from keras.models import Model
from keras.optimizers import Adam,RMSprop

In [13]:
states = Input(shape=(165,))
x = Dense(units = 85, activation='linear')(states)
y = Dense(units = 85,activation='linear')(x)
q_value = Dense(units = 1,activation='linear')(y)
ann_model = Model(inputs=states,outputs=q_value)
ann_model.compile(loss='mse',optimizer=Adam(lr=.001))

In [55]:
model_inputs = np.array(df.drop(ignore_cols+['actual_return','lift'],axis=1))
model_returns = np.array(df['actual_return'])

In [15]:
ann_model.fit(model_inputs,model_returns,epochs=100,batch_size=50)

Epoch 1/100
85799/85799 [==============================] - 4s 42us/step - loss: 9.3156e-04
Epoch 2/100
85799/85799 [==============================] - 3s 36us/step - loss: 4.1611e-04
Epoch 3/100
85799/85799 [==============================] - 3s 37us/step - loss: 3.8436e-04
Epoch 4/100
85799/85799 [==============================] - 3s 36us/step - loss: 3.5811e-04
Epoch 5/100
85799/85799 [==============================] - 3s 36us/step - loss: 3.3988e-04
Epoch 6/100
85799/85799 [==============================] - 3s 37us/step - loss: 3.3163e-04
Epoch 7/100
85799/85799 [==============================] - 3s 37us/step - loss: 3.2719e-04
Epoch 8/100
85799/85799 [==============================] - 3s 36us/step - loss: 3.2451e-04
Epoch 9/100
85799/85799 [==============================] - 3s 36us/step - loss: 3.2328e-04
Epoch 10/100
85799/85799 [==============================] - 3s 37us/step - loss: 3.2309e-04
Epoch 11/100
85799/85799 [==============================] - 3s 36us/step - loss: 3.2258e-

In [10]:
os.chdir('../Models/')

In [17]:
ann_model.save('ann_model.h5')

In [11]:
from keras.models import load_model

In [12]:
model = load_model('ann_model.h5')

In [20]:
pred_returns = [x[0] for x in model.predict(model_inputs)]

In [21]:
r2_score(y_true=model_returns,y_pred=pred_returns)

0.00757035936714423

In [22]:
df['lift_predicted'] = [max(0,np.sign(x)) for x in pred_returns]

In [23]:
accuracy_score(y_true=df['lift'],y_pred=df['lift_predicted'])

0.5222321938484131

In [24]:
precision_score(y_true=df['lift'],y_pred=df['lift_predicted'])

0.4952742574420172

In [25]:
recall_score(y_true=df['lift'],y_pred=df['lift_predicted'])

0.7455031298710938

In [26]:
df['month'] = df['Date'].apply(lambda x : str(x)[5:7])
df['year'] = df['Date'].apply(lambda x: str(x)[0:4])

In [27]:
df['correct_prediction'] = df[['lift','lift_predicted']].apply(lambda x: 1 if int(x[0]) == int(x[1]) else 0,axis=1)

In [28]:
df['precise_prediction'] = df[['lift','lift_predicted']].apply(lambda x: 1 if int(x[0]) == 1 and int(x[1]) == 1 else 0,axis=1)

In [29]:
df_grp = df.groupby(['month','year','Symbol','Sector']).agg({'lift':['count','sum'],'lift_predicted':['sum'],
                                                          'correct_prediction':['sum'],'precise_prediction':['sum']})

In [30]:
df_grp.reset_index(inplace=True)

In [31]:
df_grp.columns = ['month','year','Symbol','Sector','trade_days','price_lift','pred_price_lift','correct_predcitions','precise_predictions']

In [32]:
os.chdir('../Statistics/')

In [33]:
wb = load_workbook('report.xlsx')
writer = pd.ExcelWriter('report.xlsx',engine='openpyxl')
writer.book = wb
df_grp.to_excel(writer,sheet_name='ann_price_stats',index=False)
writer.save()
writer.close()

In [13]:
os.chdir('../Input_Data')

In [14]:
df = pd.read_csv('oot.csv',header=0)

In [15]:
rename_dict = {col : col.replace('%','pct_') for col in df.columns if '%' in col}

In [16]:
df_val = df

In [17]:
df_val.rename(rename_dict,axis=1,inplace=True)

In [18]:
df_val['lift'] = df_val['actual_return'].apply(lambda x: 1 if x >0 else 0) 

In [19]:
for col in categorical:
    for category in conversion_dict[col]:
        df_val[col+'_dum_'+str(category)] = 0
        df_val.loc[df_val[col]==category,col+'_dum_'+str(category)]=1
    print(col+' done')

Sector done


In [20]:
rename_dict = {col : col.replace(' ','_').replace('-','_').replace('&','_') for col in df.columns if '-' in col or ' ' in col}

In [21]:
df_val.rename(rename_dict,axis=1,inplace=True)

In [22]:
for col in model_columns:
    df_val[col] = df_val[col].apply(lambda x : x if np.abs(x) <= 1 else np.sign(x)*1)

In [23]:
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 165)               0         
_________________________________________________________________
dense_4 (Dense)              (None, 85)                14110     
_________________________________________________________________
dense_5 (Dense)              (None, 85)                7310      
_________________________________________________________________
dense_6 (Dense)              (None, 1)                 86        
Total params: 21,506
Trainable params: 21,506
Non-trainable params: 0
_________________________________________________________________


In [24]:
def get_equation(model):
    mat1 = np.matrix(model.layers[1].get_weights()[0])
    mat2 = np.matrix(model.layers[1].get_weights()[1])
    mat3 = np.concatenate((mat1,mat2),axis=0)
    mat4 = np.matrix(model.layers[2].get_weights()[0])
    mat5 = np.matmul(mat3,mat4)
    mat5[165,:]+=np.matrix(model.layers[2].get_weights()[1])
    mat6 = np.matrix(model.layers[3].get_weights()[0])
    mat7 = np.matmul(mat5,mat6)
    mat7[165,:]+=np.matrix(model.layers[3].get_weights()[1])
    
    return [float(x) for x in mat7[:,0]]

In [25]:
dynamic_eqn = pd.DataFrame()
dynamic_eqn['Variable'] = list(model_columns)+['intercept']
dynamic_eqn['eq0'] = get_equation(model)

In [56]:
model.predict(np.array(model_inputs[56,:]).reshape(1,165))[0][0]

0.0007458086

In [57]:
np.dot(np.array(list(model_inputs[56,:])+[1]),np.array(get_equation(model)))

0.0007458082536453525

In [26]:
dates = sorted(list(df_val['Date'].unique()))

In [27]:
os.chdir('../Models/')

In [28]:
model = load_model('ann_model.h5')

In [29]:
ann_val_stats = pd.DataFrame()
for i,date in enumerate(dates):
    df_req = df_val[df_val['Date']==date]
    model_inputs = np.array(df_req[model_columns])
    model_returns = np.array(df_req['actual_return'])
    df_req['pred_return'] = [x[0] for x in model.predict(model_inputs)]
    df_req['pred_lift'] = df_req['pred_return'].apply(lambda x : 1 if x >0 else 0)
    df_append = df_req[['Date','Symbol','Sector','actual_return','lift','pred_return']]
    ann_val_stats = ann_val_stats.append(df_append)
    model.fit(model_inputs,model_returns,batch_size=50,epochs=100)
    model.save('ann_model.h5')
    model = load_model('ann_model.h5')
    dynamic_eqn['eq'+str(i+1)] = get_equation(model)
    print('\n')
    print(dynamic_eqn)
    print('\n')
    print('{} days done'.format(i+1))
    print('\n')

C:\Users\DELL\Anaconda3\lib\site-packages\ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
C:\Users\DELL\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  import sys


Epoch 1/100
50/50 [==============================] - 0s 4ms/step - loss: 5.1820e-04
Epoch 2/100
50/50 [==============================] - 0s 100us/step - loss: 4.7274e-04
Epoch 3/100
50/50 [==============================] - 0s 60us/step - loss: 4.1417e-04
Epoch 4/100
50/50 [==============================] - 0s 60us/step - loss: 3.5985e-04
Epoch 5/100
50/50 [==============================] - 0s 80us/step - loss: 3.1404e-04
Epoch 6/100
50/50 [==============================] - 0s 40us/step - loss: 2.8178e-04
Epoch 7/100
50/50 [==============================] - 0s 60us/step - loss: 2.6539e-04
Epoch 8/100
50/50 [==============================] - 0s 60us/step - loss: 2.5987e-04
Epoch 9/100
50/50 [==============================] - 0s 60us/step - loss: 2.5687e-04
Epoch 10/100
50/50 [==============================] - 0s 80us/step - loss: 2.5220e-04
Epoch 11/100
50/50 [==============================] - 0s 60us/step - loss: 2.4700e-04
Epoch 12/100
50/50 [==============================] - 0s 60us/s

Epoch 97/100
50/50 [==============================] - 0s 60us/step - loss: 1.2224e-04
Epoch 98/100
50/50 [==============================] - 0s 60us/step - loss: 1.2185e-04
Epoch 99/100
50/50 [==============================] - 0s 80us/step - loss: 1.2147e-04
Epoch 100/100
50/50 [==============================] - 0s 60us/step - loss: 1.2108e-04


                              Variable       eq0       eq1
0                      High_pct_change  0.080299 -0.038772
1                       Low_pct_change -0.031188  0.051489
2                      Last_pct_change  0.015467  0.059495
3                      VWAP_pct_change  0.014003  0.123105
4                    Volume_pct_change -0.015600 -0.011473
5                  Turnover_pct_change  0.015622 -0.029356
6                    Trades_pct_change -0.001260 -0.015273
7        Deliverable_Volume_pct_change -0.002892  0.057240
8            pct_Deliverble_pct_change -0.002658  0.006740
9                Open_nifty_pct_change -0.003378  0.011165
10  

Epoch 50/100
50/50 [==============================] - 0s 40us/step - loss: 1.2047e-04
Epoch 51/100
50/50 [==============================] - 0s 40us/step - loss: 1.2013e-04
Epoch 52/100
50/50 [==============================] - 0s 40us/step - loss: 1.1976e-04
Epoch 53/100
50/50 [==============================] - 0s 60us/step - loss: 1.1937e-04
Epoch 54/100
50/50 [==============================] - 0s 40us/step - loss: 1.1898e-04
Epoch 55/100
50/50 [==============================] - 0s 40us/step - loss: 1.1861e-04
Epoch 56/100
50/50 [==============================] - 0s 40us/step - loss: 1.1828e-04
Epoch 57/100
50/50 [==============================] - 0s 60us/step - loss: 1.1800e-04
Epoch 58/100
50/50 [==============================] - 0s 60us/step - loss: 1.1774e-04
Epoch 59/100
50/50 [==============================] - 0s 60us/step - loss: 1.1749e-04
Epoch 60/100
50/50 [==============================] - 0s 100us/step - loss: 1.1723e-04
Epoch 61/100
50/50 [==============================] -

Epoch 1/100
50/50 [==============================] - 0s 3ms/step - loss: 6.3653e-04
Epoch 2/100
50/50 [==============================] - 0s 59us/step - loss: 4.2650e-04
Epoch 3/100
50/50 [==============================] - 0s 60us/step - loss: 2.5540e-04
Epoch 4/100
50/50 [==============================] - 0s 60us/step - loss: 2.1616e-04
Epoch 5/100
50/50 [==============================] - 0s 40us/step - loss: 2.5387e-04
Epoch 6/100
50/50 [==============================] - 0s 60us/step - loss: 2.8520e-04
Epoch 7/100
50/50 [==============================] - 0s 160us/step - loss: 2.7325e-04
Epoch 8/100
50/50 [==============================] - 0s 80us/step - loss: 2.2846e-04
Epoch 9/100
50/50 [==============================] - 0s 60us/step - loss: 1.7929e-04
Epoch 10/100
50/50 [==============================] - 0s 60us/step - loss: 1.4618e-04
Epoch 11/100
50/50 [==============================] - 0s 60us/step - loss: 1.3256e-04
Epoch 12/100
50/50 [==============================] - 0s 40us/s

...

Epoch 96/100
50/50 [==============================] - 0s 279us/step - loss: 4.7607e-05
Epoch 97/100
50/50 [==============================] - 0s 279us/step - loss: 4.7555e-05
Epoch 98/100
50/50 [==============================] - 0s 219us/step - loss: 4.7504e-05
Epoch 99/100
50/50 [==============================] - 0s 259us/step - loss: 4.7455e-05
Epoch 100/100
50/50 [==============================] - 0s 259us/step - loss: 4.7407e-05


                              Variable       eq0       eq1       eq2  \
0                      High_pct_change  0.080299 -0.038772  0.050301   
1                       Low_pct_change -0.031188  0.051489 -0.010071   
2                      Last_pct_change  0.015467  0.059495  0.077012   
3                      VWAP_pct_change  0.014003  0.123105  0.043691   
4                    Volume_pct_change -0.015600 -0.011473 -0.010342   
5                  Turnover_pct_change  0.015622 -0.029356 -0.023822   
6                    Trades_pct_change -0.001260 -0.015273

Epoch 1/100
50/50 [==============================] - 1s 18ms/step - loss: 2.2549e-04
Epoch 2/100
50/50 [==============================] - 0s 339us/step - loss: 1.9312e-04
Epoch 3/100
50/50 [==============================] - 0s 319us/step - loss: 1.4959e-04
Epoch 4/100
50/50 [==============================] - 0s 240us/step - loss: 1.1383e-04
Epoch 5/100
50/50 [==============================] - 0s 319us/step - loss: 9.2680e-05
Epoch 6/100
50/50 [==============================] - 0s 319us/step - loss: 8.3925e-05
Epoch 7/100
50/50 [==============================] - 0s 279us/step - loss: 8.2265e-05
Epoch 8/100
50/50 [==============================] - 0s 339us/step - loss: 8.3166e-05
Epoch 9/100
50/50 [==============================] - 0s 279us/step - loss: 8.4070e-05
Epoch 10/100
50/50 [==============================] - 0s 239us/step - loss: 8.3994e-05
Epoch 11/100
50/50 [==============================] - 0s 259us/step - loss: 8.2615e-05
Epoch 12/100
50/50 [==============================] -

Epoch 96/100
50/50 [==============================] - 0s 259us/step - loss: 4.0559e-05
Epoch 97/100
50/50 [==============================] - 0s 299us/step - loss: 4.0525e-05
Epoch 98/100
50/50 [==============================] - 0s 239us/step - loss: 4.0492e-05
Epoch 99/100
50/50 [==============================] - 0s 279us/step - loss: 4.0460e-05
Epoch 100/100
50/50 [==============================] - 0s 239us/step - loss: 4.0429e-05


                              Variable       eq0       eq1       eq2  \
0                      High_pct_change  0.080299 -0.038772  0.050301   
1                       Low_pct_change -0.031188  0.051489 -0.010071   
2                      Last_pct_change  0.015467  0.059495  0.077012   
3                      VWAP_pct_change  0.014003  0.123105  0.043691   
4                    Volume_pct_change -0.015600 -0.011473 -0.010342   
5                  Turnover_pct_change  0.015622 -0.029356 -0.023822   
6                    Trades_pct_change -0.001260 -0.015273

Epoch 1/100
50/50 [==============================] - 1s 18ms/step - loss: 4.9403e-04
Epoch 2/100
50/50 [==============================] - 0s 299us/step - loss: 3.8323e-04
Epoch 3/100
50/50 [==============================] - 0s 299us/step - loss: 2.7236e-04
Epoch 4/100
50/50 [==============================] - 0s 279us/step - loss: 2.1796e-04
Epoch 5/100
50/50 [==============================] - 0s 259us/step - loss: 2.1187e-04
Epoch 6/100
50/50 [==============================] - 0s 239us/step - loss: 2.1991e-04
Epoch 7/100
50/50 [==============================] - 0s 259us/step - loss: 2.1493e-04
Epoch 8/100
50/50 [==============================] - 0s 299us/step - loss: 1.9133e-04
Epoch 9/100
50/50 [==============================] - 0s 259us/step - loss: 1.6220e-04
Epoch 10/100
50/50 [==============================] - 0s 279us/step - loss: 1.4471e-04
Epoch 11/100
50/50 [==============================] - 0s 279us/step - loss: 1.4693e-04
Epoch 12/100
50/50 [==============================] -

Epoch 96/100
50/50 [==============================] - 0s 279us/step - loss: 8.5708e-05
Epoch 97/100
50/50 [==============================] - 0s 299us/step - loss: 8.5499e-05
Epoch 98/100
50/50 [==============================] - 0s 279us/step - loss: 8.5299e-05
Epoch 99/100
50/50 [==============================] - 0s 239us/step - loss: 8.5100e-05
Epoch 100/100
50/50 [==============================] - 0s 259us/step - loss: 8.4898e-05


                              Variable       eq0       eq1       eq2  \
0                      High_pct_change  0.080299 -0.038772  0.050301   
1                       Low_pct_change -0.031188  0.051489 -0.010071   
2                      Last_pct_change  0.015467  0.059495  0.077012   
3                      VWAP_pct_change  0.014003  0.123105  0.043691   
4                    Volume_pct_change -0.015600 -0.011473 -0.010342   
5                  Turnover_pct_change  0.015622 -0.029356 -0.023822   
6                    Trades_pct_change -0.001260 -0.015273

In [30]:
len(dates)

183

In [31]:
os.chdir('../Statistics/')

In [65]:
wb = load_workbook('report.xlsx')
writer = pd.ExcelWriter('report.xlsx',engine='openpyxl')
writer.book = wb
dynamic_eqn.to_excel(writer,sheet_name='ann_dyn_eqn',index=False)
writer.save()
writer.close()

In [32]:
ann_val_stats['month'] = ann_val_stats['Date'].apply(lambda x : str(x)[5:7])
ann_val_stats['year'] = ann_val_stats['Date'].apply(lambda x: str(x)[0:4])

In [33]:
ann_val_stats['pred_lift'] = ann_val_stats['pred_return'].apply(lambda x : 1 if x >0 else 0)

In [34]:
ann_val_stats['correct_prediction'] = ann_val_stats[['lift','pred_lift']].apply(lambda x: 1 if int(x[0]) == int(x[1]) else 0,axis=1)

In [35]:
ann_val_stats['precise_prediction'] = ann_val_stats[['lift','pred_lift']].apply(lambda x: 1 if int(x[0]) == 1 and int(x[1]) == 1 else 0,axis=1)

In [36]:
ann_val_grp = ann_val_stats.groupby(['month','year','Symbol','Sector']).agg({'lift':['count','sum'],'pred_lift':['sum'],
                                                          'correct_prediction':['sum'],'precise_prediction':['sum']})

In [37]:
ann_val_grp.reset_index(inplace=True)

In [38]:
ann_val_grp.columns = ['month','year','Symbol','Sector','trade_days','price_lift','pred_price_lift','correct_predcitions','precise_predictions']

In [39]:
ann_val_grp

month  year      Symbol                  Sector  trade_days  price_lift  \
0      01  2020  ADANIPORTS     Services - Shipping           2           2   
1      01  2020  ASIANPAINT          Consumer Goods           2           1   
2      01  2020    AXISBANK                 Banking           2           1   
3      01  2020  BAJAJ-AUTO              Automobile           2           0   
4      01  2020  BAJAJFINSV      Financial Services           2           1   
5      01  2020  BAJFINANCE      Financial Services           2           1   
6      01  2020  BHARTIARTL       Telecommunication           2           1   
7      01  2020        BPCL      Energy - Oil & Gas           2           0   
8      01  2020   BRITANNIA          Consumer Goods           2           1   
9      01  2020       CIPLA         Pharmaceuticals           2           0   
10     01  2020   COALINDIA                  Metals           2           1   
11     01  2020     DRREDDY         Pharmaceuticals           2           0   
12     01  2020   EICHERMOT              Automobile           2           0   
13     01  2020        GAIL      Energy - Oil & Gas           2           1   
14     01  2020      GRASIM                  Cement           2           1   
15     01  2020     HCLTECH  Information Technology           2           2   
16     01  2020        HDFC      Financial Services           2           2   
17     01  2020    HDFCBANK                 Banking           2           2   
18     01  2020  HEROMOTOCO              Automobile           2           0   
19     01  2020    HINDALCO                  Metals           2           1   
20     01  2020  HINDUNILVR          Consumer Goods           2           1   
21     01  2020  IBULHSGFIN      Financial Services           2           1   
22     01  2020   ICICIBANK                 Banking           2           1   
23     01  2020  INDUSINDBK                 Banking           2           1   
24     01  2020    INFRATEL       Telecommunication           2           1   
25     01  2020        INFY  Information Technology           2           1   
26     01  2020         IOC      Energy - Oil & Gas           2           1   
27     01  2020         ITC          Consumer Goods           2           1   
28     01  2020    JSWSTEEL                  Metals           2           1   
29     01  2020   KOTAKBANK                 Banking           2           0   
..    ...   ...         ...                     ...         ...         ...   
470    12  2019  HINDUNILVR          Consumer Goods          21           6   
471    12  2019  IBULHSGFIN      Financial Services          21           9   
472    12  2019   ICICIBANK                 Banking          21           9   
473    12  2019  INDUSINDBK                 Banking          21           8   
474    12  2019    INFRATEL       Telecommunication          21           8   
475    12  2019        INFY  Information Technology          21          14   
476    12  2019         IOC      Energy - Oil & Gas          21           9   
477    12  2019         ITC          Consumer Goods          21           7   
478    12  2019    JSWSTEEL                  Metals          21          13   
479    12  2019   KOTAKBANK                 Banking          21          12   
480    12  2019          LT            Construction          21           9   
481    12  2019         M&M              Automobile          21          10   
482    12  2019      MARUTI              Automobile          21           6   
483    12  2019        NTPC          Energy - Power          21          11   
484    12  2019        ONGC      Energy - Oil & Gas          21           8   
485    12  2019   POWERGRID          Energy - Power          21          11   
486    12  2019    RELIANCE      Energy - Oil & Gas          21           8   
487    12  2019        SBIN                 Banking          21           7   
488    12  2019   SUNPHARMA         Pharmaceuticals   

In [41]:
wb = load_workbook('report.xlsx')
writer = pd.ExcelWriter('report.xlsx',engine='openpyxl')
writer.book = wb
ann_val_grp.to_excel(writer,sheet_name='ann_oot_stats',index=False)
writer.save()
writer.close()

In [42]:
os.chdir('../Models/')

In [43]:
model.save('ann_model.h5')